# Travaux pratiques, semaine 8. 
## Factorisation LU.
Cette feuille de TP est très proche d’une feuille donnée les années précédentes.

In [4]:
# Chargement des bibliothèques
import numpy as np                # Pour faire du calcul scientifique
import matplotlib.pyplot as plt   # Pour illustrer les résultats à l’aide de graphiques

## Exercice 1 (factorisation LU)
On rappelle que le [procédé d'élimination de Gauss](https://en.wikipedia.org/wiki/Gaussian_elimination) sans échange, lorsqu'il est applicable à une matrice réelle carrée inversible $A$, s'interprète comme un [procédé de factorisation](https://en.wikipedia.org/wiki/LU_decomposition) de $A$ sous la forme d'un produit $LU$, où la matrice $L$ est triangulaire inférieure, à éléments diagonaux tous égaux à $1$ et la matrice $U$ est triangulaire supérieure.

**1.** On rappelle que si l’on peut effectuer le pivot de Gauss sans échange sur la matrice $A$, on obtient une suite de matrices $A^(k)$ dont les $k$ premières colonnes sont « triangulaires supérieures ». Les opérations sur les lignes peuvent alors être vues comme 

$$  A_k = E_{k} A_{k-1},$$

où la matrice d’élimination est donnée par 

$$E_{k}=\begin{pmatrix}
1& 0 & \cdots & \cdots & \cdots & \cdots & \cdots & 0\\
0& 1 & \ddots & & & & & \vdots\\
\vdots & \ddots & \ddots & \ddots & & & & \vdots \\
\vdots &  &0 & 1 & \ddots &  & & \vdots \\
\vdots &  & \vdots & -l_{k+1,k} & 1 & \ddots &  & \vdots \\
\vdots &  & \vdots & -l_{k+2,k} & 0 & \ddots & \ddots & \vdots \\
\vdots &  & \vdots & \vdots & \vdots & \ddots & \ddots & 0 \\
0 & \cdots & 0 & -l_{n,k}& 0 & \cdots & 0 & 1
\end{pmatrix},$$

où $l_{j,k}=\frac{a_{j,k}^{(k-1)}}{a_{k,k}}$ pour $j>k$. En notant $U=A^{(n-1)}$ et $L$ la matrice triangulaire inférieure ayant des $1$ sur la diagonale et les coefficients $l_{j,k}$ en-dessous, on peut montrer qu’on a alors $A=LU$. En pratique on peut stocker directement les coefficients de $L$ et de $U$ dans une seule matrice, en mettant dans une même matrice à chaque étape les coefficients de $A^{(k)}$, et les coefficients des $k$ premières colonnes de $L$ à la place des zéros de $A^{(k)}$.

Écrire une fonction `LU`, prenant en argument un tableau contenant une matrice carrée $A$ et retournant les coefficients des matrices $L$ et $U$ de la factorisation $A=LU$, stockés dans un tableau de même taille que celui contenant $A$. 

In [1]:
def LU(A):
    B=np.copy(A)
    for k in range(B.shape[0]-1):
        B[k+1:,k]/=B[k,k]
        B[k+1:,k+1:]-=B[k:k+1,k+1:]*B[k+1:,k:k+1]
    return B

**2.** Utiliser cette fonction pour calculer la décomposition LU de la matrice
$$
A=
\begin{pmatrix}1&4&7\\2&5&8\\3&6&10\\
\end{pmatrix}.
$$

In [48]:
A=np.array([[1.,4.,7.],[2.,5.,8.],[3.,6.,10.]])
T=LU(A.copy())

In [49]:
U=np.array([[1.,4.,7.],[0.,-3.,-6.],[0.,0.,1.]])
L=np.array([[1.,0.,0.],[2.,1.,0.],[3.,2.,1.]])
np.dot(L,U)

array([[ 1.,  4.,  7.],
       [ 2.,  5.,  8.],
       [ 3.,  6., 10.]])

In [50]:
A

array([[ 1.,  4.,  7.],
       [ 2.,  5.,  8.],
       [ 3.,  6., 10.]])

**3.** Utiliser cette factorisation pour résoudre le système linéaire $Ax=b$ avec $b=(1,1,1)^\top$. Vérifier que le résultat obtenu est correct en le comparant à celui calculé par la commande `linalg.solve(A,b)` de NumPy.

In [51]:
def LUsolve(T,b):
    n = T.shape[0]
    y = np.zeros(n)
    for i in range(n):
        y[i]=b[i]-np.dot(T[i,:i],y[:i])
    x = np.zeros(n)
    for j in range(n-1,-1,-1):
        x[j]=(y[j]-np.dot(T[j,j+1:],x[j+1:]))/T[j,j]
    return x

In [53]:
b=np.array([1.,1.,1.])
LUsolve(T,b),np.linalg.solve(A,b)

(array([-0.33333333,  0.33333333,  0.        ]),
 array([-0.33333333,  0.33333333, -0.        ]))

On considère à présent la version du procédé utilisant une stratégie de choix de pivot partiel, ce qui implique de possibles échanges de lignes lors de la factorisation.

**4.** Écrire une fonction `LUP`, prenant en argument un tableau contenant la matrice $A$ et retournant les matrices $P$, $L$ et $U$ de la factorisation $PA=LU$ correspondant à l'utilisation d'une stratégie de choix de pivot partiel. Comme précédemment, les matrices $L$ et $U$ seront toutes deux stockées dans un tableau de même taille que celui contenant $A$, et la matrice de permutation $P$ sera stockée sous la forme d'un tableau indiquant la position des lignes de $A$ dans la matrice $PA$.

**5.** Utiliser cette fonction pour la résolution du système linéaire $Ax=b$, avec
$$
A=\begin{pmatrix}3&17&10\\2&4&-2\\6&18&-12\end{pmatrix}\text{ et }b=\begin{pmatrix}1\\2\\3\end{pmatrix}.
$$
Vérifier que le résultat trouvé est correct en le comparant à celui calculé par la commande `linalg.solve(A,b)` de NumPy.

In [ ]:
A=np.array([[3.,17.,10.],[2.,4.,-2.],[6.,18.,-12.]])
b=np.array([1.,2.,3.])

## Exercice bonus (erreurs d'arrondi et conditionnement)
On veut dans cet exercice mettre en évidence les problèmes, liés à la présence d'erreurs d'arrondi dans les calculs, apparaissant lors de la résolution numérique de certains systèmes linéaires. On va pour cela considérer la famille des [matrices de Hilbert](https://en.wikipedia.org/wiki/Hilbert_matrix). Numériquement, la matrice de Hilbert $H$ d'ordre $n$ est obtenue à l’aide de la fonction `hilbert(n)` codée ci-dessous.

In [ ]:
def hilbert(n):
    return np.array([[1/(i+j+1) for i in range(n)] for j in range(n)])

**1.** Poser $n=10$ et choisir une matrice colonne non nulle $x$ à $n$ lignes (par exemple celle dont tous les éléments valent $1$). Calculer ensuite le vecteur $b=Hx$.

**2.** Résoudre alors numériquement le système $Hx=b$ en utilisant la fonction `linalg.solve` de NumPy. Que constate-t-on ? En notant $\hat{x}$ la solution calculée, comparer précisément $\hat{x}$ avec $x$ en calculant l'erreur relative
$$
\frac{\|\hat{x}-x\|_2}{\|x\|_2}.
$$ 

**3.** L'erreur relative dépend-elle fortement du choix du second membre du système linéaire ?

Pour évaluer cette dépendance, on tire une solution $x$ aléatoirement via la fonction `random.rand` de NumPy et on calcule le second membre correspondant comme dans la première question. On effectue ensuite la résolution du système linéaire ainsi obtenu et on répète plusieurs fois cette opération.

**4.** Tracer le graphe, en utilisant une échelle logarithmique pour l'axe des ordonnées, de l'erreur relative en fonction de l'ordre $n$ de la matrice de Hilbert pour la solution dont toutes les composantes sont égales à 1. Tracer sur la même figure le graphe du [conditionnement](https://en.wikipedia.org/wiki/Condition_number#Matrices) en norme $\|\cdot\|_2$ de la matrice, obtenu via la fonction `linalg.cond` de NumPy, en fonction de son ordre. Que peut-on remarquer ? 